In [2]:
import os
import pandas as pd
from pandas.tseries.offsets import QuarterEnd
from decimal import Decimal
import numpy as np
from datetime import datetime, timedelta
from dotenv import load_dotenv
import yfinance as yf


import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objs as go
import pytz  # Make sure to import pytz for timezone handling
import seaborn as sns


import requests
import csv
import json

import warnings

In [5]:
# # yahoo finance free version

# today_date = datetime.today()
# window_days = 365*10 # This is 10 years in days window

# # Define the list of stock symbols
# stocks_list = [
#     'SPY'
#     ,'CNI'
#     ,'PM'
#     # ,'COST'
#     # ,'WMT'

#     ]

# # Fetch the data
# data = yf.download(
#     stocks_list
#     ,start=today_date - timedelta(days=window_days)
#     ,end=today_date)



# # The data contains multi-level columns, we'll focus on 'Adj Close' for adjusted closing prices
# adj_close = data['Adj Close']

# # Perform standardization using StandardScaler
# scaler = StandardScaler()
# standardized_data = scaler.fit_transform(adj_close)

# # Convert the normalized data back to a DataFrame
# standardized_data = pd.DataFrame(standardized_data, index=adj_close.index, columns=adj_close.columns)


# # Plotting the adjusted closing prices of the stocks
# plt.figure(figsize=(14, 7))

# for stock in stocks_list:
#     plt.plot(standardized_data[stock], label=stock)

# plt.title('Stock Prices Over Time')
# plt.xlabel('Date')
# plt.ylabel('Adjusted Closing Price')
# plt.legend()
# plt.grid(True)
# plt.show()


In [3]:
load_dotenv()

API_KEY = os.getenv("alpha_vantage_api_key")

In [4]:
# Addtional setting session
# Set display options to show all rows and columns
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
warnings.filterwarnings("ignore")
pd.options.mode.copy_on_write = True

In [69]:
# Parameters section

alpha_vantage_api_key = API_KEY # FREE TIER API rate limit is 25 requests per day
# ticker_symbols = [
#     # 'XOM'
#     # ,'PM'
#     # ,'CNI'
#     # ,'VZ'
#     # ,'JNJ'
#     # ,'XOM'
#     # ,'WM'
#     # ,'CB'
#     # ,'TRV'
#     # ,'BRK.B'


#     # energy
#     'IVV'
#     # ,'FAST'
#     # ,'WM'
#     # ,'PG'
#     # ,'WMT'
#     # ,'CHD'
#     ,'COST'
#     ,'FANG'
#     # ,'IBN'

#  ]

ticker_symbols = [
'MCD'
,'SBUX'
,'YUM'
,'QSR'
,'DRI'
,'YUMC'
,'CAVA'
,'DPZ'
,'WING'
,'TXRH'
,'ARMK'
,'SHAK'
,'SG'
,'EAT'
,'WEN'
,'CAKE'
,'ARCO'
,'PZZA'
,'BLMN'
,'HDL'
,'CBRL'
,'KRUS'
,'PTLO'
,'JACK'
,'BJRI'
,'CHUY'
# ,'BH'
,'DIN'
,'LOCO'
,'RICK'
,'NATH'
,'DENN'
,'GENK'
,'PBPB'
,'THCH'
,'STKS'
,'FATBB'
,'FAT'
,'RRGB'
,'NDLS'
,'BDL'
,'ARKR'
,'RAVE'
,'GTIM'
,'PNST'
,'SDOT'
,'BTBD'
,'REBN'
,'YOSH'
]

window_days = 365*10
start_date = datetime.today()
end_date = start_date - timedelta(days=window_days)

stock_return_consolidate_df = pd.DataFrame()
stock_daily_ts_consolidate_df = pd.DataFrame()

# Stock Price Return Comparison

In [70]:
for symbol in ticker_symbols:

    # STOCK SPLIT FACTOR section
    url = f'https://www.alphavantage.co/query?function=SPLITS&symbol={symbol}&apikey={alpha_vantage_api_key}'
    r = requests.get(url)
    data = r.json()

    for key, value in data.items():
        if key == 'data':
            if len(value) > 0:
                stock_split_record_df = pd.DataFrame(value)
                stock_split_record_df['split_factor'] = pd.to_numeric(stock_split_record_df['split_factor'], errors='coerce') # change split_factor series to numeric data
                stock_split_record_df['effective_date'] = pd.to_datetime(stock_split_record_df['effective_date'])
            else:
                stock_split_record_df = pd.DataFrame()
                stock_split_record_df['split_factor'] = 1
                stock_split_record_df['effective_date'] = datetime.today()


    # Daily quote section
    # replace the "demo" apikey below with your own key from https://www.alphavantage.co/support/#api-key
    url = f'https://www.alphavantage.co/query?function=TIME_SERIES_DAILY&symbol={symbol}&apikey={alpha_vantage_api_key}&outputsize=full'
    r = requests.get(url)
    data = r.json()

    for key, value in data.items():
        if key == 'Time Series (Daily)':


            selected_cols = [
                '4. close'
            ]

            Daily_stock_df = pd.DataFrame(value).transpose()[selected_cols] # tranpose the dataframe and sub select selected cols

            # Rename columns
            Daily_stock_df.rename(
                columns={
                    '4. close': 'stock_price'
                    }
                ,inplace=True
                )
            
            Daily_stock_df["stock_price"] = Daily_stock_df["stock_price"].astype(str).apply(lambda x: float(x))
            Daily_stock_df["stock_price"] = Daily_stock_df["stock_price"].round(2)
            Daily_stock_df.index = pd.to_datetime(Daily_stock_df.index)


    for date_i in Daily_stock_df.index.date:
        for date_j in stock_split_record_df['effective_date'].dt.date:
            if date_i == date_j:

                # stock price to divided the split factor
                Daily_stock_df.loc[Daily_stock_df.index.date < date_j, 'stock_price'] /= (stock_split_record_df['split_factor'][stock_split_record_df['effective_date'].dt.date == date_j].values[0])


    # Dividend section
    # replace the "demo" apikey below with your own key from https://www.alphavantage.co/support/#api-key
    url = f'https://www.alphavantage.co/query?function=DIVIDENDS&symbol={symbol}&apikey={alpha_vantage_api_key}'
    r = requests.get(url)
    data = r.json()

    for key, value in data.items():
        if key == 'data':
            stock_dividend_df = pd.DataFrame(value)
            if len(value) > 0:
                stock_dividend_df = stock_dividend_df[['ex_dividend_date', 'amount']]

                # Rename columns
                stock_dividend_df.rename(
                        columns={
                            'ex_dividend_date': f'{symbol}_div_date'
                            ,'amount': f'{symbol}_div_amount'
                            }
                        ,inplace=True
                        )
                
                stock_dividend_df[f'{symbol}_div_amount'] = stock_dividend_df[f'{symbol}_div_amount'].astype(str).apply(lambda x: float(x))
                stock_dividend_df[f'{symbol}_div_amount'] = stock_dividend_df[f'{symbol}_div_amount'].round(2)
            else:
                stock_dividend_df[f'{symbol}_div_date'] = 0
                stock_dividend_df[f'{symbol}_div_amount'] = 0


    # stock_dividend_df.index = stock_dividend_df[f'{symbol}_div_date']



    # WTI oil price intervel can be daily, weekly, monthly
    url = f'https://www.alphavantage.co/query?function=WTI&interval=daily&apikey={alpha_vantage_api_key}'
    r = requests.get(url)
    data = r.json()

    for key, value in data.items():
        if key == 'data':
            WTI_daily_price_df = pd.DataFrame(value)

            # error index are the indexes which doesnot have a valid price, it shows '.'
            error_index = WTI_daily_price_df[WTI_daily_price_df['value']=='.'].index

            # Calculate the average of the previous and next prices
            previous_WTI_price = WTI_daily_price_df.loc[error_index + 1, 'value']
            next_WTI_price = WTI_daily_price_df.loc[error_index - 1, 'value']
            average_WTI_price = (previous_WTI_price + next_WTI_price) / 2

            # Update the DataFrame with the calculated average price
            WTI_daily_price_df.loc[error_index, 'value'] = average_WTI_price

            # transfer the string value to decimal
            WTI_daily_price_df['value'] = WTI_daily_price_df['value'].astype(str).apply(lambda x: float(x))

            WTI_daily_price_df.rename(
                columns={
                    'value':'WTI'
                    ,'date':'Date'
                }
                ,inplace=True
            )

            WTI_daily_price_df['Date'] = pd.to_datetime(WTI_daily_price_df['Date'])





    # Time window filter applied
    Daily_stock_df_filter_timewindow = Daily_stock_df[(Daily_stock_df.index.date >= end_date.date())
                                                & (Daily_stock_df.index.date <= start_date.date())
                                                ]
    
    stock_dividend_df_filter_timewindow = stock_dividend_df[(pd.to_datetime(stock_dividend_df[f'{symbol}_div_date']) >= pd.to_datetime(end_date))
                                                    & (pd.to_datetime((stock_dividend_df[f'{symbol}_div_date'])) <= pd.to_datetime(start_date))
                                                    ]
    

#     # Calculate the return %
#     # return including dividend = (current_price - initial_price + total_dividend_during_period) / initial_price
    stock_return = round(
        (
            (
                Daily_stock_df_filter_timewindow[f'stock_price'][0] 
                - Daily_stock_df_filter_timewindow[f'stock_price'][-1] 
                + stock_dividend_df_filter_timewindow[f'{symbol}_div_amount'].sum()
            ) 
            / Daily_stock_df_filter_timewindow[f'stock_price'][-1]
        )
    ,4
    )

    # assign value to columns in consolidate dataframe
    stock_return_consolidate_df.loc[0,f'{symbol}_{window_days/365}_yrs_return'] = stock_return
    stock_daily_ts_consolidate_df[f'{symbol}'] = Daily_stock_df_filter_timewindow[f'stock_price']


####### WTI merge step ###########
# Step to merge the WTI crude oil price into the stock_daily_ts_consolidate_df
stock_daily_ts_consolidate_df = stock_daily_ts_consolidate_df.merge(
    WTI_daily_price_df
    ,left_on=stock_daily_ts_consolidate_df.index
    ,right_on='Date'
    ,how='left'
    )

# clean the merged WTI dataframe 
stock_daily_ts_consolidate_df.index = stock_daily_ts_consolidate_df['Date']
stock_daily_ts_consolidate_df = stock_daily_ts_consolidate_df.drop(
    columns='Date'
) \

####### WTI merge step ###########


stock_daily_ts_consolidate_normalized_df = stock_daily_ts_consolidate_df / stock_daily_ts_consolidate_df.iloc[-1]

In [71]:
stock_return_consolidate_df.transpose().sort_values(
    by=stock_return_consolidate_df.transpose().columns[0]
    ,ascending=False
    )

0
WING_10.0_yrs_return   12.7983
TXRH_10.0_yrs_return    5.8804
DPZ_10.0_yrs_return     4.8571
KRUS_10.0_yrs_return    3.2489
DRI_10.0_yrs_return     3.1663
RICK_10.0_yrs_return    3.1028
MCD_10.0_yrs_return     2.8760
SBUX_10.0_yrs_return    2.0791
CAVA_10.0_yrs_return    2.0119
WEN_10.0_yrs_return     1.9041
YUM_10.0_yrs_return     1.6306
QSR_10.0_yrs_return     1.4491
SHAK_10.0_yrs_return    1.3536
ARMK_10.0_yrs_return    1.2822
YUMC_10.0_yrs_return    0.9392
ARCO_10.0_yrs_return    0.9320
NATH_10.0_yrs_return    0.8117
EAT_10.0_yrs_return     0.7330
BDL_10.0_yrs_return     0.4912
PZZA_10.0_yrs_return    0.4840
CHUY_10.0_yrs_return    0.2249
BLMN_10.0_yrs_return    0.0921
CAKE_10.0_yrs_return    0.0680
BJRI_10.0_yrs_return    0.0209
CBRL_10.0_yrs_return   -0.0624
JACK_10.0_yrs_return   -0.1120
ARKR_10.0_yrs_return   -0.1444
DENN_10.0_yrs_return   -0.1957
HDL_10.0_yrs_return    -0.2014
SG_10.0_yrs_return     -0.2416
DIN_10.0_yrs_return    -0.3196
STKS_10.0_yrs_return   -0.3301
FATBB_10.0_yrs_return  -0.3386
PBPB_10.0_yrs_return   -0.3406
FAT_10.0_yrs_return    -0.3622
GENK_10.0_yrs_return   -0.4778
GTIM_10.0_yrs_return   -0.4851
LOCO_10.0_yrs_return   -0.5676
PTLO_10.0_yrs_return   -0.5784
BTBD_10.0_yrs_return   -0.6484
RAVE_10.0_yrs_return   -0.6598
YOSH_10.0_yrs_return   -0.8525
THCH_10.0_yrs_return   -0.8903
RRGB_10.0_yrs_return   -0.9009
SDOT_10.0_yrs_return   -0.9171
REBN_10.0_yrs_return   -0.9315
PNST_10.0_yrs_return   -0.9345
NDLS_10.0_yrs_return   -0.9467

In [72]:
stock_daily_ts_consolidate_normalized_df = stock_daily_ts_consolidate_df / stock_daily_ts_consolidate_df.iloc[-1]


# Create a Plotly figure
fig = go.Figure()

# Add traces for each stock
for column in stock_daily_ts_consolidate_normalized_df.columns:
    fig.add_trace(go.Scatter(
        x=stock_daily_ts_consolidate_normalized_df.index,
        y=stock_daily_ts_consolidate_normalized_df[column],
        mode='lines',
        name=column
    ))

# Customize layout
fig.update_layout(
    title=f'Normalized Stock Prices in {window_days/365} years',
    xaxis_title='Date',
    yaxis_title='Normalized Price',
    legend_title='Stock',
    template='plotly_white'
)

# Show the plot
fig.show()

# EPS TTM Comparison

In [73]:
# Parameters section

alpha_vantage_api_key = API_KEY # FREE TIER API rate limit is 25 requests per day

# # Consumer Staples
# ticker_symbols = [
#     'MO',
#     'ADM',
#     # 'BF.B', # DATA ISSUE
#     'BG',
#     'CPB',
#     'CHD',
#     'CLX',
#     'KO',
#     'CL',
#     'CAG',
#     'STZ',
#     'COST',
#     'DG',
#     'DLTR',
#     'EL',
#     'GIS',
#     'HSY',
#     'HRL',
#     'K',
#     # 'KVUE',
#     'KDP',
#     'KMB',
#     # 'KHC',
#     'KR', 
#     # 'LW',
#     'MKC', 
#     'TAP',
#     'MDLZ',
#     'MNST',
#     # 'PEP',
#     'PM',
#     'PG',
#     'SJM',
#     'SYY',
#     'TGT',
#     'TSN',
#     'WBA',
#     'WMT'
# ]


# Energy
# ticker_symbols = [
# 'APA'
# ,'BKR'
# ,'CVX'
# ,'COP'
# ,'CTRA'
# ,'DVN'
# ,'FANG'
# ,'EOG'
# ,'EQT'
# ,'XOM'
# ,'HAL'
# ,'HES'
# ,'KMI'
# ,'MRO'
# ,'MPC'
# ,'OXY'
# ,'OKE'
# ,'PSX'
# ,'SLB'
# ,'TRGP'
# ,'VLO'
# ,'WMB'
# ]


# # Consumer Dis
# ticker_symbols = [
# # 'ABNB'
# 'AMZN'
# # ,'APTV'
# ,'AZO'
# ,'BBY'
# ,'BKNG'
# ,'BWA'
# ,'CZR'
# ,'KMX'
# ,'CCL'
# ,'CMG'
# ,'DRI'
# ,'DECK'
# ,'DPZ'
# ,'DHI'
# ,'EBAY'
# ,'EXPE'
# ,'F'
# ,'GRMN'
# # ,'GM'
# ,'GPC'
# ,'HAS'
# # ,'HLT'
# ,'HD'
# ,'LVS'
# ,'LEN'
# ,'LKQ'
# ,'LOW'
# # ,'LULU'
# ,'MAR'
# ,'MCD'
# ,'MGM'
# ,'MHK'
# ,'NKE'
# # ,'NCLH'
# ,'NVR'
# ,'ORLY'
# ,'POOL'
# ,'PHM'
# ,'RL'
# ,'ROST'
# ,'RCL'
# ,'SBUX'
# ,'TPR'
# # ,'TSLA'
# ,'TJX'
# ,'TSCO'
# # ,'ULTA'
# ,'WYNN'
# ,'YUM'    
# ]

# # Consumer Dis / Restuarants
# ticker_symbols = [
# 'MCD'
# ,'SBUX'
# ,'YUM'
# ,'QSR'
# ,'DRI'
# ,'YUMC'
# ,'CAVA'
# ,'DPZ'
# ,'WING'
# ,'TXRH'
# ,'ARMK'
# ,'SHAK'
# ,'SG'
# ,'EAT'
# ,'WEN'
# ,'CAKE'
# ,'ARCO'
# ,'PZZA'
# ,'BLMN'
# ,'HDL'
# ,'CBRL'
# ,'KRUS'
# ,'PTLO'
# ,'JACK'
# ,'BJRI'
# ,'CHUY'
# # ,'BH'
# ,'DIN'
# ,'LOCO'
# ,'RICK'
# ,'NATH'
# ,'DENN'
# ,'GENK'
# ,'PBPB'
# ,'THCH'
# ,'STKS'
# ,'FATBB'
# ,'FAT'
# ,'RRGB'
# ,'NDLS'
# ,'BDL'
# ,'ARKR'
# ,'RAVE'
# ,'GTIM'
# ,'PNST'
# ,'SDOT'
# ,'BTBD'
# ,'REBN'
# ,'YOSH'
# ]

# Consumer Non-Durables / Food: Specialty/Candy
ticker_symbols = [
'LSF'
,'CHSN'
,'JVA'
,'FRPT'
,'STKL'
,'SOWG'
,'IFF'
,'K'
,'KLG'
,'INGR'
,'SXT'
,'BCPC'
,'POST'
,'UTZ'
,'BROS'
,'MKC'
,'PETZ'
,'KDP'
,'NOMD'
,'BRCC'
,'CPB'
,'SENEB'
,'ASH'
,'SENEA'
,'JJSF'
,'PEP'
,'LANC'
,'FLO'
,'SJM'
,'TR'
,'THS'
,'HSY'
,'JBSS'
,'BOF'
,'FARM'
,'BRID'
,'LW'
,'DAR'
,'WEST'
,'RMCF'
,'SNAX'
,'PLAG'
,'NUZE'

]


window_period = 20 # years
current_year = datetime.today().year
start_year = current_year - window_period

current_date = pd.Timestamp(datetime.today()).normalize()  # Start with today's date
current_date_prevQtr = start_date + QuarterEnd(-2) 
qtr_range = pd.date_range(start=f'{start_year}-03-31', end=start_date, freq='Q')


stock_consolidate_annual_eps_df = pd.DataFrame()
stock_consolidate_ttm_eps_df = pd.DataFrame()

stock_consolidate_annual_eps_df['fiscalDateEnding'] = [i for i in range(start_year, current_year)]
stock_consolidate_ttm_eps_df['fiscalDateEnding'] = qtr_range
# stock_consolidate_ttm_eps_df.sort_index(ascending=False, inplace=True)

In [74]:
# for i in ticker_symbols:
#     print(i)

In [75]:
# Earning section
# past earnings from alpha vintage API
for j, symbol in enumerate(ticker_symbols):
    print(j, symbol)
    url = f'https://www.alphavantage.co/query?function=EARNINGS&symbol={symbol}&apikey={alpha_vantage_api_key}'
    r = requests.get(url)
    data = r.json()

    for key, value in data.items():
        if key == 'annualEarnings':

            selected_cols = [
                'fiscalDateEnding'
                ,'reportedEPS'
            ]

            annualEPS_df = pd.DataFrame(value) # tranpose the dataframe and sub select selected cols


            annualEPS_df['fiscalDateEnding'] = pd.to_datetime(annualEPS_df['fiscalDateEnding']).dt.year

            annualEPS_df = annualEPS_df[
                annualEPS_df['fiscalDateEnding'].isin(
                    range(
                        (datetime.today().year - window_period) 
                        ,datetime.today().year
                            )
                            )
                            ]

            # Convert the column to decimal type
            for col in selected_cols:
                if col in ['reportedEPS']:
                    annualEPS_df[f'{col}'] = annualEPS_df[f'{col}'].astype(str).apply(lambda x: float(x))

                else:
                    continue
            
            # clean annualEPS_df
            annualEPS_df = annualEPS_df.sort_values('reportedEPS', ascending=False).drop_duplicates('fiscalDateEnding')
            annualEPS_df = annualEPS_df.sort_values('fiscalDateEnding', ascending=True).reset_index(drop=True)
            annualEPS_df.rename(
                columns={
                    'reportedEPS': f'{symbol}_EPS'
                }
                ,inplace=True
            )

        if key == 'quarterlyEarnings':

            selected_cols = [
                'fiscalDateEnding'
                ,'reportedEPS'
            ]

            qtrEPS_df = pd.DataFrame(value)[selected_cols] # tranpose the dataframe and sub select selected cols
            qtrEPS_df['fiscalDateEnding'] = pd.to_datetime(qtrEPS_df['fiscalDateEnding'])

            qtrEPS_df = qtrEPS_df.sort_values(['fiscalDateEnding'], ascending=True)
            # Calculate the EPS TTM by summing the current quarter and the previous 3 quarters
            qtrEPS_df[f'{symbol}_EPS_TTM'] = qtrEPS_df['reportedEPS'].rolling(window=4).sum().fillna(0)

            # filtered based on window_period years
            qtrEPS_df = qtrEPS_df[qtrEPS_df['fiscalDateEnding'] >= pd.Timestamp(f'{start_year}-03-31')]

            qtrEPS_df = qtrEPS_df.drop(columns=['reportedEPS'])



            # consolidation
            stock_consolidate_annual_eps_df = pd.merge(
                stock_consolidate_annual_eps_df
                ,annualEPS_df
                ,left_on='fiscalDateEnding'
                ,right_on='fiscalDateEnding'
                ,how='left'
            ).fillna(0)

            stock_consolidate_ttm_eps_df = pd.merge(
                stock_consolidate_ttm_eps_df
                ,qtrEPS_df
                ,left_on='fiscalDateEnding'
                ,right_on='fiscalDateEnding'
                ,how='left'
            ).fillna(0)

0 LSF
1 CHSN
2 JVA
3 FRPT
4 STKL
5 SOWG
6 IFF
7 K
8 KLG
9 INGR
10 SXT
11 BCPC
12 POST
13 UTZ
14 BROS
15 MKC
16 PETZ
17 KDP
18 NOMD
19 BRCC
20 CPB
21 SENEB
22 ASH
23 SENEA
24 JJSF
25 PEP
26 LANC
27 FLO
28 SJM
29 TR
30 THS
31 HSY
32 JBSS
33 BOF
34 FARM
35 BRID
36 LW
37 DAR
38 WEST
39 RMCF
40 SNAX
41 PLAG
42 NUZE


In [79]:
stock_consolidate_annual_eps_df

fiscalDateEnding  LSF_EPS  CHSN_EPS  JVA_EPS  FRPT_EPS  STKL_EPS  IFF_EPS  \
0               2004     0.00      0.00   0.0000    0.0000    0.1934     2.28   
1               2005     0.00      0.00   0.0460    0.0000    0.1700     1.96   
2               2006     0.00      0.00   0.1256    0.0000    0.2000     2.40   
3               2007     0.00      0.00   0.1690    0.0000    0.0000     2.65   
4               2008     0.00      0.00  -0.4683    0.0000    0.1200     2.76   
5               2009     0.00      0.00   0.6048    0.0000   -0.0042     2.70   
6               2010     0.00      0.00   0.4379    0.0000    0.2900     3.37   
7               2011     0.00      0.00   0.1359    0.0000    0.1166     3.74   
8               2012     0.00      0.00   0.3770    0.0000    0.3558     3.99   
9               2013     0.00      0.00  -0.2300    0.0000    0.2411     4.47   
10              2014     0.00      0.00   0.7649   -0.2200    0.3228     5.08   
11              2015     0.00      0.00  -0.2267   -0.1000   -0.1649     5.25   
12              2016     0.00      0.00   0.3635   -0.0800    0.0700     5.50   
13              2017     0.00      0.00   0.0844   -0.1300   -1.5625     5.89   
14              2018     0.00      0.00   0.1928   -0.1527   -0.2800     6.21   
15              2019     0.00      0.00   0.0000   -0.0600   -0.0109     6.17   
16              2020    -1.61      0.13   0.1686   -0.0563    0.7672     5.70   
17              2021    -2.65     -0.01   0.0300   -0.6700   -0.0057     5.67   
18              2022    -4.02      0.00  -0.6500   -1.3000    0.1023     5.56   
19              2023    -1.09      0.00  -0.7131   -0.7100   -1.2390     3.34   

    K_EPS  KLG_EPS  INGR_EPS  SXT_EPS  BCPC_EPS  POST_EPS  UTZ_EPS  BROS_EPS  \
0    2.14     0.00      1.46     1.53    0.3100      0.00   0.0000    0.0000   
1    2.36     0.00      1.19     1.21    0.4014      0.00   0.0000    0.0000   
2    2.50     0.00      1.63     1.43    0.4500      0.00   0.0000    0.0000   
3    2.75     0.00      2.54     1.65    0.5900      0.00   0.0000    0.0000   
4    2.99     0.00      3.58     1.89    0.6800      0.00   0.0000    0.0000   
5    3.16     0.00      2.00     1.78    0.9336      0.00   0.0000    0.0000   
6    3.29     0.00      3.24     2.17    1.1200      0.00   0.0000    0.0000   
7    3.38     0.00      4.69     2.41    1.2900      0.00   0.0000    0.0000   
8    3.26     0.00      5.58     2.58    1.3300      1.61   0.0000    0.0000   
9    3.77     0.00      5.06     2.71    1.4700      0.95   0.0000    0.0000   
10   3.81     0.00      5.21     3.01    1.7000     -0.36   0.0000    0.0000   
11   3.54     0.00      5.89     3.04    2.5100      0.05   0.0000    0.0000   
12   3.76     0.00      7.10     3.22    2.5200      2.62   0.0000    0.0000   
13   4.04     0.00      7.71     3.42    2.5400      2.68   0.0000    0.0000   
14   4.34     0.00      6.91     3.55    3.0200      4.08   0.0343    0.0000   
15   3.94     0.00      6.63     2.96    3.1900      4.97   0.1412    0.0000   
16   4.00     0.00      6.23     2.80    3.3200      2.74   0.7807    0.5827   
17   4.17     0.00      6.66     3.14    3.5700      2.38   0.5500    0.9127   
18   4.23     0.00      7.45     3.34    4.0400      2.07   0.5500    0.1500   
19   4.16     1.39      9.42     2.87    3.9900      5.33   0.5700    0.2422   

    MKC_EPS  PETZ_EPS  KDP_EPS  NOMD_EPS  BRCC_EPS  CPB_EPS  SENEB_EPS  \
0      0.77    0.0000     0.00    0.0000    0.0000     1.57     1.8755   
1      0.82    0.0000     0.00    0.0000    0.0000     1.71     0.3855   
2      0.87    0.0000     0.00    0.0000    0.0000     1.82     1.9514   
3      0.98    0.0000     0.00    0.0000    0.0000     1.93     0.0000   
4      1.08    0.0000     1.84    0.0000    0.0000     2.08     2.5458   
5      1.17    0.0000     1.97    0.0000    0.0000     2.20     1.5354   
6      1.34    0.0000     2.41    0.0000    0.0000     2.48     3.9100   
7      1.40    0.0000     2.8

In [81]:

stock_consolidate_annual_eps_df = stock_consolidate_annual_eps_df[stock_consolidate_annual_eps_df['fiscalDateEnding'] >= 2005]
# Assuming stock_consolidate_annual_eps_df is your DataFrame
# Create a copy of the DataFrame for normalization
stock_consolidate_annual_eps_normalized_df = stock_consolidate_annual_eps_df.copy()

# List of columns to normalize
ticker_symbol_cols = stock_consolidate_annual_eps_normalized_df.columns.to_list()
ticker_symbol_cols.remove('fiscalDateEnding')

# Function to normalize based on the first non-zero value
def normalize_column(column):
    # Find the first non-zero value
    first_non_zero = column[column != 0].iloc[0]
    return column / first_non_zero

# Normalize each EPS column
for col in ticker_symbol_cols:
    stock_consolidate_annual_eps_normalized_df[col] = normalize_column(stock_consolidate_annual_eps_normalized_df[col])

In [82]:
stock_consolidate_annual_eps_normalized_df

fiscalDateEnding   LSF_EPS  CHSN_EPS    JVA_EPS  FRPT_EPS  STKL_EPS  \
1               2005 -0.000000  0.000000   1.000000 -0.000000  1.000000   
2               2006 -0.000000  0.000000   2.730435 -0.000000  1.176471   
3               2007 -0.000000  0.000000   3.673913 -0.000000  0.000000   
4               2008 -0.000000  0.000000 -10.180435 -0.000000  0.705882   
5               2009 -0.000000  0.000000  13.147826 -0.000000 -0.024706   
6               2010 -0.000000  0.000000   9.519565 -0.000000  1.705882   
7               2011 -0.000000  0.000000   2.954348 -0.000000  0.685882   
8               2012 -0.000000  0.000000   8.195652 -0.000000  2.092941   
9               2013 -0.000000  0.000000  -5.000000 -0.000000  1.418235   
10              2014 -0.000000  0.000000  16.628261  1.000000  1.898824   
11              2015 -0.000000  0.000000  -4.928261  0.454545 -0.970000   
12              2016 -0.000000  0.000000   7.902174  0.363636  0.411765   
13              2017 -0.000000  0.000000   1.834783  0.590909 -9.191176   
14              2018 -0.000000  0.000000   4.191304  0.694091 -1.647059   
15              2019 -0.000000  0.000000   0.000000  0.272727 -0.064118   
16              2020  1.000000  1.000000   3.665217  0.255909  4.512941   
17              2021  1.645963 -0.076923   0.652174  3.045455 -0.033529   
18              2022  2.496894  0.000000 -14.130435  5.909091  0.601765   
19              2023  0.677019  0.000000 -15.502174  3.227273 -7.288235   

     IFF_EPS     K_EPS  KLG_EPS  INGR_EPS   SXT_EPS   BCPC_EPS  POST_EPS  \
1   1.000000  1.000000      0.0  1.000000  1.000000   1.000000  0.000000   
2   1.224490  1.059322      0.0  1.369748  1.181818   1.121076  0.000000   
3   1.352041  1.165254      0.0  2.134454  1.363636   1.469856  0.000000   
4   1.408163  1.266949      0.0  3.008403  1.561983   1.694071  0.000000   
5   1.377551  1.338983      0.0  1.680672  1.471074   2.325859  0.000000   
6   1.719388  1.394068      0.0  2.722689  1.793388   2.790234  0.000000   
7   1.908163  1.432203      0.0  3.941176  1.991736   3.213752  0.000000   
8   2.035714  1.381356      0.0  4.689076  2.132231   3.313403  1.000000   
9   2.280612  1.597458      0.0  4.252101  2.239669   3.662182  0.590062   
10  2.591837  1.614407      0.0  4.378151  2.487603   4.235177 -0.223602   
11  2.678571  1.500000      0.0  4.949580  2.512397   6.253114  0.031056   
12  2.806122  1.593220      0.0  5.966387  2.661157   6.278027  1.627329   
13  3.005102  1.711864      0.0  6.478992  2.826446   6.327853  1.664596   
14  3.168367  1.838983      0.0  5.806723  2.933884   7.523667  2.534161   
15  3.147959  1.669492      0.0  5.571429  2.446281   7.947185  3.086957   
16  2.908163  1.694915      0.0  5.235294  2.314050   8.271051  1.701863   
17  2.892857  1.766949      0.0  5.596639  2.595041   8.893871  1.478261   
18  2.836735  1.792373      0.0  6.260504  2.760331  10.064773  1.285714   
19  1.704082  1.762712      1.0  7.915966  2.371901   9.940209  3.310559   

      UTZ_EPS  BROS_EPS   MKC_EPS    PETZ_EPS   KDP_EPS  NOMD_EPS   BRCC_EPS  \
1    0.000000  0.000000  1.000000    0.000000  0.000000 -0.000000   0.000000   
2    0.000000  0.000000  1.060976    0.000000  0.000000 -0.000000   0.000000   
3    0.000000  0.000000  1.195122    0.000000  0.000000 -0.000000   0.000000   
4    0.000000  0.000000  1.317073    0.000000  1.000000 -0.000000   0.000000   
5    0.000000  0.000000  1.426829    0.000000  1.070652 -0.000000   0.000000   
6    0.000000  0.000000  1.634146    0.000000  1.309783 -0.000000   0.000000   
7    0.000000  0.000000  1.707317    0.000000  1.521739 -0.000000   0.000000   
8    0.000000  0.000000  1.865854    0.000000  1.586957 -0.000000   0.000000   
9    0.000000  0.000000  1.926829    0.000000  1.750000 -0.000000   0.000000   
10   0.000000  0.000000  2.024390    0.000000  1.989130 -0.000000   0.000000   
11   0.000000  0.000000  2.134146    1.000000  2.184783  1.000000   0.000000   
12   0.000000  0.00000

In [60]:
fig = px.line(stock_consolidate_annual_eps_normalized_df, 
              x='fiscalDateEnding', 
              y=ticker_symbol_cols, 
              labels={'value':'Normalized EPS', 'fiscalDateEnding':'Year'}, 
              title='Normalized EPS Comparison Over Time')

# Add markers to the lines
fig.update_traces(mode='lines+markers')

# Set log scale for the y-axis
fig.update_layout(
    yaxis_type="log",  # This sets the y-axis to log scale
    xaxis_title='Fiscal Year',
    yaxis_title='EPS Value (Log Scale)',
    legend_title='Company',
    hovermode='x unified'
)

fig.show()

In [80]:
stock_consolidate_ttm_eps_df

fiscalDateEnding  LSF_EPS_TTM  CHSN_EPS_TTM  JVA_EPS_TTM  FRPT_EPS_TTM  \
0        2004-03-31         0.00           0.0          0.0        0.0000   
1        2004-06-30         0.00           0.0          0.0        0.0000   
2        2004-09-30         0.00           0.0          0.0        0.0000   
3        2004-12-31         0.00           0.0          0.0        0.0000   
4        2005-03-31         0.00           0.0          0.0        0.0000   
5        2005-06-30         0.00           0.0          0.0        0.0000   
6        2005-09-30         0.00           0.0          0.0        0.0000   
7        2005-12-31         0.00           0.0          0.0        0.0000   
8        2006-03-31         0.00           0.0          0.0        0.0000   
9        2006-06-30         0.00           0.0          0.0        0.0000   
10       2006-09-30         0.00           0.0          0.0        0.0000   
11       2006-12-31         0.00           0.0          0.0        0.0000   
12       2007-03-31         0.00           0.0          0.0        0.0000   
13       2007-06-30         0.00           0.0          0.0        0.0000   
14       2007-09-30         0.00           0.0          0.0        0.0000   
15       2007-12-31         0.00           0.0          0.0        0.0000   
16       2008-03-31         0.00           0.0          0.0        0.0000   
17       2008-06-30         0.00           0.0          0.0        0.0000   
18       2008-09-30         0.00           0.0          0.0        0.0000   
19       2008-12-31         0.00           0.0          0.0        0.0000   
20       2009-03-31         0.00           0.0          0.0        0.0000   
21       2009-06-30         0.00           0.0          0.0        0.0000   
22       2009-09-30         0.00           0.0          0.0        0.0000   
23       2009-12-31         0.00           0.0          0.0        0.0000   
24       2010-03-31         0.00           0.0          0.0        0.0000   
25       2010-06-30         0.00           0.0          0.0        0.0000   
26       2010-09-30         0.00           0.0          0.0        0.0000   
27       2010-12-31         0.00           0.0          0.0        0.0000   
28       2011-03-31         0.00           0.0          0.0        0.0000   
29       2011-06-30         0.00           0.0          0.0        0.0000   
30       2011-09-30         0.00           0.0          0.0        0.0000   
31       2011-12-31         0.00           0.0          0.0        0.0000   
32       2012-03-31         0.00           0.0          0.0        0.0000   
33       2012-06-30         0.00           0.0          0.0        0.0000   
34       2012-09-30         0.00           0.0          0.0        0.0000   
35       2012-12-31         0.00           0.0          0.0        0.0000   
36       2013-03-31         0.00           0.0          0.0        0.0000   
37       2013-06-30         0.00           0.0          0.0        0.0000   
38       2013-09-30         0.00           0.0          0.0        0.0000   
39       2013-12-31         0.00           0.0          0.0        0.0000   
40       2014-03-31         0.00           0.0          0.0        0.0000   
41       2014-06-30         0.00           0.0          0.0        0.0000   
42       2014-09-30         0.00           0.0          0.0        0.0000   
43       2014-12-31         0.00           0.0          0.0        0.0000   
44       2015-03-31         0.00           0.0          0.0        0.0000   
45       2015-06-30         0.00           0.0          0.0       -0.3500   
46       2015-09-30         0.00           0.0          0.0       -0.2600   
47       2015-12-31         0.00           0.0          0.0       -0.1000   
48       2016-03-31         0.00           0.0          0.0       -0.0600   
49       2016-06-30         0.00           0.0          0.0       -0.1100   
50       2016-09-30         0.00           0.0          0.0       -0.0400   

# SP500 Sectors

In [14]:
# Function to get the list of S&P 500 companies and their sectors
def get_sp500_companies():
    # Fetch the S&P 500 company symbols and sectors from a reliable source (e.g., Wikipedia)
    url = 'https://en.wikipedia.org/wiki/List_of_S%26P_500_companies'
    tables = pd.read_html(url)
    
    # Extract the relevant table containing the company symbols and sectors
    sp500_df = tables[0]
    
    # Return the DataFrame containing S&P 500 companies and sectors
    return sp500_df[['Symbol', 'GICS Sector', 'GICS Sub-Industry']]


# Function to create a dictionary of sectors and sub-sectors
def create_sector_subsector_dict(df):
    sector_subsector_dict = {}
    for index, row in df.iterrows():
        sector = row['GICS Sector']
        subsector = row['GICS Sub-Industry']
        if sector not in sector_subsector_dict:
            sector_subsector_dict[sector] = [subsector]
        else:
            sector_subsector_dict[sector].append(subsector)
    return sector_subsector_dict

# Function to filter the S&P 500 companies by sector
def company_sector_list(df, sector):
    return df[df['GICS Sector'] == sector]['Symbol'].tolist()

def company_sub_sector_list(df, sub_sector):
    return df[df['GICS Sub-Industry'] == sub_sector]['Symbol'].tolist()


# Get the list of S&P 500 companies and their sectors
sp500_df  = get_sp500_companies()

sp500_companies_sectors = sp500_df ['GICS Sector'].value_counts().index
sp500_companies_sub_sectors = sp500_df ['GICS Sub-Industry'].value_counts().index

sector_subsector_dict = create_sector_subsector_dict(sp500_df)


# Function to create a DataFrame from the sector_subsector_dict
def create_sector_dataframe():
    # Create a list to store dictionacompany_sector_listries representing each row of data
    data = []
    
    # Filter the DataFrame to get stocks in the specified sector
    for sector in sp500_companies_sectors:
        sector_stocks_list = company_sector_list(sp500_df, sector)

        # Iterate over the stocks in the sector and create a dictionary for each
        for i, ticker in enumerate(sector_stocks_list, start=1):
            # Create a dictionary for the current stock in the sector
            row_data = {'Sector': sector, 'Ticker': ticker}
            # Append the dictionary to the list
            data.append(row_data)
    
    # Create a DataFrame from the list of dictionaries
    df = pd.DataFrame(data)
    return df


sector_subsector_dict = create_sector_subsector_dict(sp500_df)


sector_ticker_df = create_sector_dataframe()

In [15]:
# Pivot the DataFrame
pivot_sector_ticker_df = sector_ticker_df.groupby('Sector')['Ticker'].apply(list).reset_index()

# Transpose to get sectors as columns
pivot_sector_ticker_df = pivot_sector_ticker_df.set_index('Sector').T

pivot_sector_ticker_df

Sector                             Communication Services  \
Ticker  [GOOGL, GOOG, T, CHTR, CMCSA, EA, FOXA, FOX, I...   

Sector                             Consumer Discretionary  \
Ticker  [ABNB, AMZN, APTV, AZO, BBY, BKNG, BWA, CZR, K...   

Sector                                   Consumer Staples  \
Ticker  [MO, ADM, BF.B, BG, CPB, CHD, CLX, KO, CL, CAG...   

Sector                                             Energy  \
Ticker  [APA, BKR, CVX, COP, CTRA, DVN, FANG, EOG, EQT...   

Sector                                         Financials  \
Ticker  [AFL, ALL, AXP, AIG, AMP, AON, ACGL, AJG, AIZ,...   

Sector                                        Health Care  \
Ticker  [ABT, ABBV, A, ALGN, AMGN, BAX, BDX, TECH, BII...   

Sector                                        Industrials  \
Ticker  [MMM, AOS, ALLE, AMTM, AME, ADP, AXON, BA, BR,...   

Sector                             Information Technology  \
Ticker  [ACN, ADBE, AMD, AKAM, APH, ADI, ANSS, AAPL, A...   

Sector                                          Materials  \
Ticker  [APD, ALB, AMCR, AVY, BALL, CE, CF, CTVA, DOW,...   

Sector                                        Real Estate  \
Ticker  [ARE, AMT, AVB, BXP, CPT, CBRE, CSGP, CCI, DLR...   

Sector                                          Utilities  
Ticker  [AES, LNT, AEE, AEP, AWK, ATO, CNP, CMS, ED, C...

In [16]:
sp500_sectors_dict = {}

In [17]:
for col in pivot_sector_ticker_df.columns:
    sp500_sectors_dict[col] = pivot_sector_ticker_df[col].iloc[0]

In [18]:
for key, value in sp500_sectors_dict.items():
    print(key, value)

Communication Services ['GOOGL', 'GOOG', 'T', 'CHTR', 'CMCSA', 'EA', 'FOXA', 'FOX', 'IPG', 'LYV', 'MTCH', 'META', 'NFLX', 'NWSA', 'NWS', 'OMC', 'PARA', 'TMUS', 'TTWO', 'VZ', 'DIS', 'WBD']
Consumer Discretionary ['ABNB', 'AMZN', 'APTV', 'AZO', 'BBY', 'BKNG', 'BWA', 'CZR', 'KMX', 'CCL', 'CMG', 'DRI', 'DECK', 'DPZ', 'DHI', 'EBAY', 'EXPE', 'F', 'GRMN', 'GM', 'GPC', 'HAS', 'HLT', 'HD', 'LVS', 'LEN', 'LKQ', 'LOW', 'LULU', 'MAR', 'MCD', 'MGM', 'MHK', 'NKE', 'NCLH', 'NVR', 'ORLY', 'POOL', 'PHM', 'RL', 'ROST', 'RCL', 'SBUX', 'TPR', 'TSLA', 'TJX', 'TSCO', 'ULTA', 'WYNN', 'YUM']
Consumer Staples ['MO', 'ADM', 'BF.B', 'BG', 'CPB', 'CHD', 'CLX', 'KO', 'CL', 'CAG', 'STZ', 'COST', 'DG', 'DLTR', 'EL', 'GIS', 'HSY', 'HRL', 'K', 'KVUE', 'KDP', 'KMB', 'KHC', 'KR', 'LW', 'MKC', 'TAP', 'MDLZ', 'MNST', 'PEP', 'PM', 'PG', 'SJM', 'SYY', 'TGT', 'TSN', 'WBA', 'WMT']
Energy ['APA', 'BKR', 'CVX', 'COP', 'CTRA', 'DVN', 'FANG', 'EOG', 'EQT', 'XOM', 'HAL', 'HES', 'KMI', 'MRO', 'MPC', 'OXY', 'OKE', 'PSX', 'SLB', 'TRG